## data

In [1]:
import pandas as pd

# 数据读取
data = pd.read_csv('./AI_Human.csv')
data


C:\Users\ASUS\AppData\Roaming\Python\Python311\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


text  generated
0       Cars. Cars have been around since they became ...        0.0
1       Transportation is a large necessity in most co...        0.0
2       "America's love affair with it's vehicles seem...        0.0
3       How often do you ride in a car? Do you drive a...        0.0
4       Cars are a wonderful thing. They are perhaps o...        0.0
...                                                   ...        ...
487230  Tie Face on Mars is really just a big misunder...        0.0
487231  The whole purpose of democracy is to create a ...        0.0
487232  I firmly believe that governments worldwide sh...        1.0
487233  I DFN't agree with this decision because a LFT...        0.0
487234  Richard Non, Jimmy Carter, and Bob Dole and ot...        0.0

[487235 rows x 2 columns]

In [2]:
import json
# 提取人类文本 (generated=0.0)
human_texts = data[data['generated'] == 0.0]['text'].tolist()

# 提取 AI 文本 (generated=1.0)
ai_texts = data[data['generated'] == 1.0]['text'].tolist()

# 保存为 JSON 文件
with open('human.json', 'w', encoding='utf-8') as f:
    json.dump(human_texts, f, ensure_ascii=False, indent=4)

with open('AI.json', 'w', encoding='utf-8') as f:
    json.dump(ai_texts, f, ensure_ascii=False, indent=4)

print("人类文本数量:", len(human_texts))
print("AI 生成文本数量:", len(ai_texts))

人类文本数量: 305797
AI 生成文本数量: 181438


## rewrite

In [3]:
import json
import random
from openai import OpenAI
from tenacity import retry, stop_after_attempt, wait_random_exponential

# ✅ 初始化 DeepSeek API 客户端
client = OpenAI(
    api_key="sk-02f85c18644c4cabbcad55f0961122f0",
    base_url="https://api.deepseek.com"
)

debug = False  # 是否只处理一条
SAMPLE_SIZE = 2000  # 随机挑选的数据量
REWRITE_PROMPT = "Reword the following passage to include repetitive phrases or patterns typical of AI-generated content"  # 统一的改写指令

# ✅ 自动重试机制
@retry(wait=wait_random_exponential(min=1, max=60), stop=stop_after_attempt(6))
def GPT_self_prompt(prompt_str, content_to_be_detected):
    response = client.chat.completions.create(
        model="deepseek-chat",
        messages=[
            {"role": "user", "content": f"{prompt_str}: {content_to_be_detected}"}
        ],
        stream=False
    )
    spit_out = response.choices[0].message.content.strip()
    print(spit_out)
    return spit_out

# ✅ 加载AI生成文本并随机抽样
with open('AI.json', 'r', encoding='utf-8') as file:
    ai_texts = json.load(file)
    
sampled_ai_texts = random.sample(ai_texts, min(SAMPLE_SIZE, len(ai_texts)))  # 随机选2000条


In [4]:
# ✅ 主函数：用统一指令改写文本
def rewrite_to_human_style(input_texts):
    all_data = []
    for cc, text in enumerate(input_texts):
        print(f"Processing {cc + 1}/{len(input_texts)}")
        tmp_dict = {'original_ai_text': text}
        
        try:
            # 使用统一的人类风格改写指令
            tmp_dict['human_style_rewrite'] = GPT_self_prompt(REWRITE_PROMPT, text)
        except Exception as e:
            print(f"❌ Error at index {cc}: {e}")
            tmp_dict['human_style_rewrite'] = "ERROR"
        
        all_data.append(tmp_dict)
        if debug:
            break

    return all_data

# ✅ 处理AI文本改写
ai_rewritten = rewrite_to_human_style(sampled_ai_texts)

# ✅ 保存结果
with open('ai_rewritten_in_moreAI_style.json', 'w', encoding='utf-8') as file:
    json.dump(ai_rewritten, file, indent=4, ensure_ascii=False)

print(f"完成！已处理 {len(ai_rewritten)} 条AI生成文本的改写。")

Processing 1/2000
Here’s your reworded passage with repetitive phrases and patterns typical of AI-generated content:  

---

**Have you ever felt overwhelmed with the amount of homework you have to complete?** Or perhaps you have ever struggled to find a quiet and conducive environment to study in? If so, then a homework club at your school could be just what you need.  

**One of the main advantages of having a homework club is the time it provides for students to complete their assignments.** With the distractions of home life and other extracurricular activities, it can be difficult to find the time and focus to finish homework assignments to the best of your ability. By attending a homework club, you can set aside dedicated time each day to work on your assignments, free from distractions and interruptions.  

**Additionally, homework clubs can provide a supportive and collaborative environment for students to work on their assignments.** If you're struggling with a particular topi

Here’s your reworded passage with repetitive phrases and patterns typical of AI-generated content:  

---  

**Dear Senator,**  

I am writing to express my opinion on the current system of electing the President of the United States. As a student in grade 8, I have been learning about the Electoral College and the debate surrounding it. It is important to note that it is important to consider the pros and cons of both the Electoral College and the popular vote systems before making a decision.  

One of the main arguments in favor of the Electoral College is that the Electoral College ensures that smaller states have a voice in the election. Without the Electoral College, larger states with more population would have a greater influence, which would mean that smaller states could be ignored. For example, in the 2016 presidential election, Trump won 304 electoral votes while Clinton won 227. However, Clinton received nearly 3 million more popular votes than Trump. This demonstrates tha

Here’s your reworded passage with repetitive AI-style phrasing and patterns:  

---  

**Sure King! Here’s my essay response:**  

**Do We Have KO Live Other People’s Experiences?**  

As I sit here thinking about this question, I can’t help but wonder—do we really have KO live other people’s experiences? It’s like, I get it, everyone has their own struggles and challenges, but do we really have KO go through them too? I mean, shouldn’t we be able KO just focus on our own lives and experiences?  

I think about my friends who are going through rough times right now, and I want KO help them out, but sometimes I feel like I’m just getting dragged down with them. It’s like, I get it, they’re going through a hard time, but I don’t have KO go through it too. I have my own stuff going on, you know? And sometimes I feel like I’m just getting lost in their problems.  

And then there are people who are going through way worse things than I am. Like, have you seen the news lately? There are peo

Certainly! Here’s a reworded version with repetitive phrasing and patterns often found in AI-generated content:  

---  

When it comes to advice and wisdom, it is important to recognize the value of listening to the elders. It is important to consider the insights they can provide. Take, for example, Generic_Name and Grandma—both have a wealth of life experience to offer. It is worth noting that Generic_Name may have valuable insight into areas such as career choices, investments, and other modern-day matters. It is also worth noting that Grandma, on the other hand, may offer wisdom related to topics like family dynamics, social situations, and moral guidance.  

It is important to remember that both have different perspectives, yet both perspectives are equally valuable. It is important to acknowledge that their advice could prove beneficial to someone seeking guidance. It is worth emphasizing that listening to the wisdom of those more experienced can be an incredibly useful resource

Here’s your reworded passage with repetitive AI-like phrasing and patterns:  

---  

**Fly there!** So, let’s dive into this fascinating topic: asking one person versus multiple people for advice. It’s truly an interesting topic, and when it comes to advice, it’s truly something worth exploring. After all, who doesn’t love getting advice from others, right? It’s truly a universal experience.  

**Personally, I’ve found** that asking one person for advice can be really helpful. It’s truly a great way to get focused input. For example, when I’m trying to decide which TV show to watch, my best friend is always the first person I go to. She’s truly got great taste in shows, and she’s always willing to share her opinions with me. It’s truly like having a personal TV critic!  

**On the other hand,** asking multiple people for advice can also be really helpful. It’s truly a great way to gather diverse perspectives. For instance, when I was deciding which college to apply to, my parents were

...

Certainly! Here’s a reworded version with repetitive phrasing and patterns often found in AI-generated content:  

---  

**Distance learning is a popular alternative to in-person classes at school**, offering **more flexible class schedules** and allowing students to learn **from the comfort of their own homes**. **While online learning can generally be more convenient and cost-effective**, there are **some potential drawbacks, as well**. **For instance, distance learning may lack the social aspect of traditional school**. **In-person classes often give students the opportunity to connect with their peers and teachers**, providing **collaborative learning experiences**. **In addition, it can be more difficult to stay motivated with distance learning**, as students don’t have **structured environments or built-in support systems**.  

**On the other hand, distance learning can provide more freedom and flexibility** for students with busy schedules. **With more advanced technology, onli

Certainly! Here’s a reworded version of your passage with repetitive phrasing and patterns often found in AI-generated content:  

---  

**When making important decisions, it is important to consult with multiple people before making a final decision.** By seeking input from multiple sources, you can gain a more well-rounded understanding of your options and their potential outcomes. **By gathering diverse perspectives, you can make a decision that takes into account different viewpoints.**  

**People come from different backgrounds, experiences, values, and priorities, which shape how they perceive the world.** If you only consult one person, you only get one perspective on the situation. **However, by talking to multiple people, you may uncover important details or implications that the first person missed due to their own unique perspective.** **By seeking advice from a variety of sources, you increase the chances of identifying unforeseen factors that could influence your choice.

Here’s your passage reworded with repetitive AI-like phrasing and patterns for that unmistakable "generated" feel:  

---  

**Hey there!** Let me just say, I’m *so, so* excited to be writing this essay! 😃 Being active and working toward a goal is, like, *super, super* important, you know? I mean, it’s not like just sitting around doing nothing has, like, *any, any* real purpose or anything. 🙄  

So, here’s the thing: when you’re always doing something, you’re, like, *constantly, constantly* learning and growing as a person. Like, *seriously, seriously*—think about it! When you’re playing sports or learning a new skill, you’re not just, like, *standing, standing* around doing nothing. You’re, like, *actively, actively* improving yourself and getting better at something. And that’s, like, *really, really* cool! 😎  

For *example, example*, let’s say you want to learn how to play the guitar. You could just, like, *sit, sit* around and watch YouTube videos all day, but that’s not gonna he

Here’s a reworded version of your passage with repetitive phrases and patterns typical of AI-generated content:  

---  

**"Making Mona Lisa Smile"** is an article that discusses a groundbreaking technology known as the **Facial Action Coding System**, a system that can identify human emotions. This means that computers can now utilize this system to analyze and interpret human emotions by examining facial expressions. I believe that implementing this technology in a classroom setting to monitor the emotional expressions of students could prove highly beneficial for several reasons.  

**First and foremost**, the **Facial Action Coding System** could assist teachers in gauging student reactions to specific topics. For instance, if a teacher is delivering a history lesson and observes that some students appear bored, they could adjust the lesson or make it more engaging to maintain student interest. This would not only make learning more enjoyable but also enhance comprehension of the 

Certainly! Below is a reworded version of your passage with repetitive phrases and patterns typical of AI-generated content:  

---  

**After careful consideration and thorough research**, we have compiled a comprehensive list of impactful ways students could take part in helping the community in our area. **It is important to note that** we propose our school undertake a meaningful project aimed at supporting those in need, including but not limited to the homeless, hungry individuals, and animals. **It is worth mentioning that** we believe this presents a valuable opportunity to engage students while providing mutual benefits for both the students and the local community.  

**In terms of implementation**, the project would consist of organizing regular community service initiatives. **More specifically**, this would involve activities such as volunteering at soup kitchens, fundraising for charitable causes, or assisting at animal shelters. **Furthermore**, the funds raised could th

In [5]:
#获取未被选中的文本
remaining_ai = [text for text in ai_texts if text not in sampled_ai_texts]
# ✅ 保存结果
with open('remaining_ai.json', 'w', encoding='utf-8') as file:
    json.dump(remaining_ai, file, indent=4, ensure_ascii=False)
#不能再运行了，否则sampled_ai_texts将变了

In [6]:
import json

# 加载 ai_rewritten_in_human_style.json
with open('remaining_ai.json', 'r', encoding='utf-8') as f:
    ai_rewritten = json.load(f)

# 加载 human.json
with open('ai_rewritten_in_moreAI_style.json', 'r', encoding='utf-8') as f:
    human_texts = json.load(f)

# 打印数量
print("remaining_ai.json 中的总数:", len(ai_rewritten))
print("ai_rewritten_in_moreAI_style.json 中的总数:", len(human_texts))


remaining_ai.json 中的总数: 179438
ai_rewritten_in_moreAI_style.json 中的总数: 2000


In [7]:
import json
import random

# 读取 remaining_ai.json
with open("remaining_ai.json", "r", encoding="utf-8") as f:
    remaining_ai = json.load(f)

SAMPLE_SIZE=2000
sampled_remaining_ai = random.sample(remaining_ai, min(SAMPLE_SIZE, len(remaining_ai)))  # 随机选2000条

# 读取 ai_rewritten_in_human_style.json
with open("ai_rewritten_in_moreAI_style.json", "r", encoding="utf-8") as f:
    ai_rewritten = json.load(f)
rewritten_texts = [item['human_style_rewrite'] for item in ai_rewritten if isinstance(item, dict) and 'human_style_rewrite' in item]
ai_rewritten = rewritten_texts#字典转化为字符

# 合并两个列表
combined_data = sampled_remaining_ai + ai_rewritten

# 保存为新文件 combined_ai_data.json
with open("combined_ai_data.json", "w", encoding="utf-8") as f:
    json.dump(combined_data, f, ensure_ascii=False, indent=2)

print(f"合并完成，共 {len(combined_data)} 条数据。")
#2000条attack，2000条未attack

合并完成，共 4000 条数据。


In [9]:
import json
import csv

# 1. 读取 combined_ai_data.json
with open("combined_ai_data.json", "r", encoding="utf-8") as f:
    ai_data = json.load(f)

# 每条加上 label = 'ai'
ai_labeled = [{"text": text, "label": "1"} for text in ai_data if isinstance(text, str)]

# 2. 读取 human.json
with open("human.json", "r", encoding="utf-8") as f:
    human_data = json.load(f)

SAMPLE_SIZE=8000
sampled_human_data = random.sample(human_data, min(SAMPLE_SIZE, len(human_data)))  # 随机选8000条

# 每条加上 label = 'human'
human_labeled = [{"text": text, "label": "0"} for text in sampled_human_data if isinstance(text, str)]

# 3. 合并
final_data = ai_labeled + human_labeled

# 4. 写入 CSV 文件
with open("./enhanceded_ai_human.csv", "w", newline="", encoding="utf-8") as f:
    writer = csv.DictWriter(f, fieldnames=["text", "label"])
    writer.writeheader()
    writer.writerows(final_data)

print(f"CSV 写入完成，合计 {len(final_data)} 条数据。")
data1 = pd.read_csv('./enhanceded_ai_human.csv')
data1#4000AI,8000human

CSV 写入完成，合计 12000 条数据。


text  label
0       In his famous quote, Thomas Jefferson advised...      1
1      Nowadays, people make their advertisements sh ...      1
2      Cell phones. Love 'em or hate 'em, they're her...      1
3      With the development of our country's economic...      1
4       IP today's fast paced world, it's becoming in...      1
...                                                  ...    ...
11995  Deal: Principal,\n\nI personally don't mind co...      0
11996  The Seagoing Cowboy program is hard work But i...      0
11997  In the years of 1976, a spacecraft snapped pho...      0
11998  You may think that the landform that resembles...      0
11999  Should drivers be able to be on their phone wh...      0

[12000 rows x 2 columns]